In [47]:
import pandas as pd
import numpy as np
import config
import json
import requests

import plotly.graph_objects as go
import plotly.io as pio
import plotly.offline as pyo
import plotly.express as px
px.set_mapbox_access_token("pk.eyJ1IjoidG9ueXBhcmswMDEiLCJhIjoiY2t2dWVramFmODZqaDJucXBrbnhpZ2JreCJ9.-XXf1YI8YESgWbWODhZAZA")

import fiona
import geopandas as gpd

#from urllib.request import urlopen

import warnings
# warnings.filterwarnings("ignore")

## (1) Import Datasets

In [2]:
data = pd.read_json("https://nycdsacapstone2021.blob.core.windows.net/geojsons/school_districts_simplified.json")

In [3]:
#import geoJSON of school boundaries
gdf = gpd.GeoDataFrame.from_features(data["features"])
gdf.head()

geometry STATEFP UNSDLEA    GEOID  \
0  POLYGON ((-77.00244 38.96567, -77.11976 38.934...      11   00030  1100030   
1  POLYGON ((-82.65855 29.83014, -82.65630 29.564...      12   00030  1200030   
2  POLYGON ((-82.41891 30.58177, -82.45979 30.584...      12   00060  1200060   
3  POLYGON ((-86.00077 30.10360, -85.58962 29.837...      12   00090  1200090   
4  POLYGON ((-82.14258 30.14312, -82.31338 29.954...      12   00120  1200120   

                                  NAME LSAD LOGRADE HIGRADE  MTFCC SDTYP  \
0  District of Columbia Public Schools   00      PK      12  G5420         
1       Alachua County School District   00      PK      12  G5420         
2         Baker County School District   00      PK      12  G5420         
3           Bay County School District   00      PK      12  G5420         
4      Bradford County School District   00      PK      12  G5420         

  FUNCSTAT       ALAND      AWATER     INTPTLAT      INTPTLON GEO_YEAR  \
0        E   158316124    18709762  +38.9042474  -077.0165167     2021   
1        E  2267905452   241297386  +29.6757403  -082.3572210     2021   
2        E  1515738971     9686120  +30.3244416  -082.3022838     2021   
3        E  1964874033  1833915193  +30.1373956  -085.6286886     2021   
4        E   761368537    16898784  +29.9523863  -082.1666983     2021   

  SCHOOLYEAR  
0  2020-2021  
1  2020-2021  
2  2020-2021  
3  2020-2021  
4  2020-2021

In [41]:
#import df school districts demographics
mapping_df = pd.read_csv('https://nycdsacapstone2021.blob.core.windows.net/mapping/mapping_data.csv', index_col= 0).drop(['first_word'], axis = 1)
mapping_df['GEOID'] = mapping_df['GEOID'].astype('int')
mapping_df

index                      school_district  avg_rating  total_enrollment  \
0       42  District of Columbia Public Schools         5.7             48218   
1       71                              Alachua         5.0             29834   
2      312                                Baker         5.2              5060   
3       97                                  Bay         4.9             23100   
4       26                              Brevard         5.8             73331   
..     ...                                  ...         ...               ...   
476    607               Webster County Schools         4.2              1315   
477    476                Wetzel County Schools         4.5              2527   
478    657                  Wirt County Schools         3.0              1010   
479    163                  Wood County Schools         6.3             12423   
480    375               Wyoming County Schools         4.9              3947   

     num_schools  avg_pct_low_income state              school_district_id  \
0            104                81.2    DC                             NaN   
1             60                52.2    FL  Alachua County School District   
2              7                33.6    FL    Baker County School District   
3             38                58.4    FL      Bay County School District   
4            100                49.7    FL  Brevard County School District   
..           ...                 ...   ...                             ...   
476            4                69.8    WV  Webster County School District   
477            9                53.6    WV   Wetzel County School District   
478            3                50.7    WV     Wirt County School District   
479           28                52.2    WV     Wood County School District   
480           13                50.2    WV  Wyoming County School District   

       GEOID  
0    1100030  
1    1200030  
2    1200060  
3    1200090  
4    1200150  
..       ...  
476  5401530  
477  5401560  
478  5401590  
479  5401620  
480  5401650  

[481 rows x 9 columns]

In [46]:
#add possible additional columns?
#mapping_df['num_schools_scale']= np.log10(mapping_df['num_schools'])

In [48]:
#import historical transactions
historical = pd.read_csv('https://nycdsacapstone2021.blob.core.windows.net/mapping/historical_cleaned.csv', index_col= 0)


# (2) Maps

### Boundary Maps

In [45]:
fig = px.choropleth_mapbox(
        mapping_df, geojson=gdf, color="avg_pct_low_income",
        locations="GEOID", featureidkey="properties.GEOID",hover_name = "school_district_id" ,opacity=0.7, zoom=2)

fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.update_geos(fitbounds="locations", visible=False)
fig.show()

## Scatterplots on map:
- scatter of SMH properties within a radius 
- scatter of current redfin listings with a radius
- ability to filter
- maybe filter on cluster

In [49]:
fig = (
    px.scatter_mapbox(
        historical[historical["PRICE"]<250000],
        lat="LATITUDE",
        lon="LONGITUDE",
        color="STATUS", 
        size="Log_price"
    )
    .update_traces(marker={"size": 10})
    .update_layout(
        mapbox={
            "style": "open-street-map",
            "zoom": 5,
            "layers": [
                {
                    "source": json.loads(gdf.geometry.to_json()),
                    "below": "traces",
                    "type": "line",
                    "color": "blue",
                    "line": {"width": 1.5},
                }
            ],
        },
        margin={"l": 0, "r": 0, "t": 0, "b": 0},
    )
)
fig.show()